In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objs as go
import sklearn
import optuna
from pandas_profiling import ProfileReport
from sklearn.decomposition import PCA
from sklearn.metrics import ndcg_score
from sklearn.model_selection import cross_val_score
from sklearn.feature_selection import SelectFromModel
from sklearn.preprocessing import LabelEncoder
from sklearn.impute import KNNImputer
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import VotingClassifier, RandomForestClassifier
from xgboost.sklearn import XGBClassifier

import lightgbm as lgb
import warnings
warnings.filterwarnings("ignore")
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 100)

C:\Study\Python\Anaconda\lib\site-packages\dask\dataframe\utils.py:14: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [2]:
# read in files
raw_age_df = pd.read_csv("age_gender_bkts.csv")
raw_country_df = pd.read_csv("countries.csv")
raw_session_df = pd.read_csv('sessions.csv')
raw_train_df = pd.read_csv('train_users_2.csv')
raw_test_df = pd.read_csv("test_users.csv")

# EDA

## Age and gender information

In [3]:
print('age_bucket: ', raw_age_df['age_bucket'].unique())
print('year: ', raw_age_df['year'].unique())
print('country_destination: ', raw_age_df['country_destination'].unique())

age_bucket:  ['100+' '95-99' '90-94' '85-89' '80-84' '75-79' '70-74' '65-69' '60-64'
 '55-59' '50-54' '45-49' '40-44' '35-39' '30-34' '25-29' '20-24' '15-19'
 '10-14' '5-9' '0-4']
year:  [2015.]
country_destination:  ['AU' 'CA' 'DE' 'ES' 'FR' 'GB' 'IT' 'NL' 'PT' 'US']


In [4]:
# overall destinations distribution
by_country_df = raw_age_df.groupby(['country_destination'])['population_in_thousands'].sum().reset_index()
fig = px.bar(by_country_df, x='country_destination', y='population_in_thousands', color='population_in_thousands', 
             color_continuous_scale="darkmint")
fig.show()

In [5]:
# destinations by gender
by_gender_df = raw_age_df.groupby(['gender', 'country_destination'])['population_in_thousands'].sum().reset_index()
fig = px.bar(by_gender_df, x='country_destination', y='population_in_thousands', color='gender', barmode = 'group',
             color_continuous_scale="darkmint")
fig.show()

In [6]:
# overall age distribution
by_age_df = raw_age_df.groupby(['age_bucket'])['population_in_thousands'].sum().reset_index()
fig = px.bar(by_age_df, x='age_bucket', y='population_in_thousands', color='population_in_thousands', 
             color_continuous_scale="reds")
fig.show()

In [7]:
# destination distribution by age
by_age_df = raw_age_df.groupby(['age_bucket', 'country_destination'])['population_in_thousands'].sum().reset_index()
fig = px.bar(by_age_df, x='country_destination', y='population_in_thousands', color='age_bucket', barmode = 'group',
             color_continuous_scale="darkmint")
fig.show()
# compared with overall age distribution, DE and IT has more middle aged people, ie 45-60

## Country Info

In [8]:
raw_country_df
# nothing special here, so no eda for countries

country_destination  lat_destination  lng_destination  distance_km  \
0                  AU       -26.853388       133.275160   15297.7440   
1                  CA        62.393303       -96.818146    2828.1333   
2                  DE        51.165707        10.452764    7879.5680   
3                  ES        39.896027        -2.487694    7730.7240   
4                  FR        46.232193         2.209667    7682.9450   
5                  GB        54.633220        -3.432277    6883.6590   
6                  IT        41.873990        12.564167    8636.6310   
7                  NL        52.133057         5.295250    7524.3203   
8                  PT        39.553444        -7.839319    7355.2534   
9                  US        36.966427       -95.844030       0.0000   

   destination_km2 destination_language   language_levenshtein_distance  
0        7741220.0                   eng                           0.00  
1        9984670.0                   eng                           0.00  
2         357022.0                   deu                          72.61  
3         505370.0                   spa                          92.25  
4         643801.0                   fra                          92.06  
5         243610.0                   eng                           0.00  
6         301340.0                   ita                          89.40  
7          41543.0                   nld                          63.22  
8          92090.0                   por                          95.45  
9        9826675.0                   eng                           0.00

## Sessions

In [9]:
report = ProfileReport(raw_session_df, title = 'session report')
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [10]:
session_df = raw_session_df[['user_id']].dropna().drop_duplicates().set_index('user_id')
# count total actions for each user
session_df['action_count'] = raw_session_df.groupby('user_id')['action'].count()
# count total time spent (in seconds)
session_df['total_secs'] = raw_session_df.groupby('user_id')['secs_elapsed'].sum()

book_df = raw_train_df[['id', 'country_destination']].merge(session_df[['action_count', 'total_time']], 
                                                            left_on = 'id', right_index = True, how = 'left')
print('Not book: ', book_df.loc[book_df['country_destination'] == 'NDF', ['action_count', 'total_time']].mean())
print('Book: ', book_df.loc[book_df['country_destination'] != 'NDF', ['action_count', 'total_time']].mean())

KeyError: "['total_time'] not in index"

In [ ]:
session_by_country_df = book_df.groupby(['country_destination'])[['action_count', 'total_time']].mean().reset_index()
fig = px.bar(session_by_country_df, x='country_destination', y='action_count', color='action_count', 
             color_continuous_scale="greens")
fig.show()
fig = px.bar(session_by_country_df, x='country_destination', y='total_time', color='total_time', 
             color_continuous_scale="blues")
fig.show()
# People who go to IT spend most time and take most actions
# People who do not book spend least time and take lesat actions

## Train dataset

In [ ]:
report = ProfileReport(raw_train_df, title = 'train')
report

In [ ]:
train_df = raw_train_df.copy()
train_df.loc[train_df['age'] > 1000, 'age'] = (2015 - train_df['age'])
train_df.loc[train_df['age'] > 100, 'age'] = np.nan
fig = px.box(train_df, x = 'country_destination', y = 'age', color = 'country_destination')
fig.show()
train_df.loc[train_df['gender'] == '-unknown-', 'gender'] = np.nan
tmp_df = train_df.groupby(['country_destination', 'gender'])['id'].count().reset_index()
fig = px.bar(tmp_df, x = 'country_destination', y = 'id', color = 'gender', barmode = 'group')
fig.show()

In [ ]:
# language
lang_df = train_df[['language', 'country_destination']].value_counts().unstack().fillna(0.0)
lang_df['sum'] = lang_df.sum(axis = 1)
for language in lang_df.index:
    lang_df.loc[language] = lang_df.loc[language]/lang_df.loc[language, 'sum']
lang_df

We can observe that people are more likely to go to the country which speak the same language.

For example for language de(German), 3.3% people go the DE(Germany). While for the language en, only 0.5% people go to Germany. So language has some meanings.

# Cleaning and Feature Engineering

## Sessions

In [8]:
session_df = raw_session_df[['user_id']].dropna().drop_duplicates().set_index('user_id')
# count total actions for each user
session_df['action_count'] = raw_session_df.groupby('user_id')['action'].count()
# count total time spent (in seconds)
session_df['total_secs'] = raw_session_df.groupby('user_id')['secs_elapsed'].sum()

# count each action and time of each action

tmp_df = raw_session_df.groupby(['user_id', 'action']).agg({'user_id': 'count', 'action': 'nunique', 'secs_elapsed': 'sum'})\
                       .rename(columns = {'user_id': 'count', 'action': 'nunique', 'secs_elapsed': 'sec'}).unstack()
cols = []
for level0 in tmp_df.columns.levels[0]:
    for level1 in tmp_df.columns.levels[1]:
        cols.append(level1 + '_' + level0)
tmp_df.columns = cols
session_df = pd.concat([session_df, tmp_df], axis = 1)

# choose most frequently used device
raw_session_df.loc[raw_session_df['device_type'].isin(['Linux Desktop', 'Tablet', 'Chromebook', 'Blackberry', 'iPodtouch',
                                                       'Windows Phone', 'Opera Phone']), 'device_type'] = 'other'
raw_session_df['device_type'].fillna('-unknown-', inplace = True)
device_df = raw_session_df.groupby(['user_id', 'device_type'])[['device_type']].count()\
                          .rename(columns = {'device_type': 'device'}).sort_values('device').reset_index()\
                          .drop_duplicates(['user_id'], keep= 'last').set_index('user_id').drop(columns = 'device')
session_df = pd.concat([session_df, device_df], axis = 1)

del tmp_df

## Age and Gender

In [9]:
# Users in different age tend to choose different destination
# Calculate the probabilities of choosing different destinations for different age buckets
age_df = raw_age_df.copy()
by_age_df = age_df.groupby(['age_bucket', 'country_destination'])['population_in_thousands'].sum().unstack()
by_age_df.columns = by_age_df.columns.map(lambda x: 'by_age_' + x)
by_age_df['sum'] = by_age_df.sum(axis = 1)

for col in by_age_df.columns:
    by_age_df[col] = by_age_df[col]/by_age_df['sum']
by_age_df.drop(columns = ['sum'], inplace = True)

## Train and Test

In [47]:
# Combine train test
df = pd.concat([raw_train_df, raw_test_df]).reset_index().drop(columns = 'index')
# Convert timestamp to date
df['first_active_date'] = pd.to_datetime(df['timestamp_first_active'].astype(str).map(lambda x: x[:4] + '-' + x[4:6] + '-' + x[6:8]))
df.drop(columns = 'timestamp_first_active', inplace = True)
# gender
df.loc[df['gender'] == '-unknown-', 'gender'] = np.nan
df['gender'] = df['gender'].str.lower()
# age
df.loc[df['age'] > 1000, 'age'] = (2015 - df['age'])
df.loc[~df['age'].between(16, 100), 'age'] = np.nan
df['age'].fillna(df['age'].median(), inplace = True)
# determine if the system language is the same as destination language
df['language'] = df['language'].str.upper()
df.loc[df['language'] == '-UNKNOWN-', 'language'] = 'EN'
for destination in ['US', 'FR', 'CA', 'GB', 'ES', 'IT', 'PT', 'NL', 'DE', 'AU']:
    if (destination in ['US', 'CA', 'GB', 'AU']):
        df.loc[df['language'] == 'EN', 'dlanguage_EN'] = 1
    else:
        df.loc[df['language'] == destination, f'dlanguage_{destination}'] = 1
df.loc[df[[f'dlanguage_{x}' for x in ['EN', 'FR', 'ES', 'IT', 'PT', 'NL', 'DE']]].sum(axis = 1) == 0, 'dlanguage_other'] = 1

# date features
df['create_month'] = pd.to_datetime(df['date_account_created']).dt.month
df['create_day'] = pd.to_datetime(df['date_account_created']).dt.day
df['create_dow'] = pd.to_datetime(df['date_account_created']).dt.dayofweek
df['first_month'] = pd.to_datetime(df['first_active_date']).dt.month
df['first_day'] = pd.to_datetime(df['first_active_date']).dt.day
df['first_dow'] = pd.to_datetime(df['first_active_date']).dt.dayofweek

# set small categories as 'other' to decrease features
signup_flow = df['signup_flow'].value_counts()
df.loc[df['signup_flow'].isin(signup_flow[signup_flow < 1000].index), 'signup_flow'] = 'other'
df['signup_flow'] = df['signup_flow'].astype(str)
affiliate_provider = df['affiliate_provider'].value_counts()
df.loc[df['affiliate_provider'].isin(affiliate_provider[affiliate_provider < 100].index), 'affiliate_provider'] = 'other'
first_affiliate_tracked = df['first_affiliate_tracked'].value_counts()
df.loc[df['first_affiliate_tracked'].isin(first_affiliate_tracked[first_affiliate_tracked < 1000].index), 'first_affiliate_tracked'] = 'other'
first_browser = df['first_browser'].value_counts()
df.loc[df['first_browser'].isin(first_browser[first_browser < 1000].index), 'first_browser'] = 'other'

df['action_before_account'] = (df['first_active_date'] < pd.to_datetime(df['date_account_created'])).astype(int)
df['is_apple'] = (df['first_device_type'].isin(['Mac Desktop', 'iPhone', 'iPad'])).astype(int)

# fillna
df[['gender', 'first_affiliate_tracked']] = df[['gender', 'first_affiliate_tracked']].fillna('-unknown-')
df[[f'dlanguage_{x}' for x in ['EN', 'FR', 'ES', 'IT', 'PT', 'NL', 'DE', 'other']]] = df[[f'dlanguage_{x}' for x in ['EN', 'FR', 'ES', 'IT', 'PT', 'NL', 'DE', 'other']]].fillna(0)

print(df.isna().sum())

id                              0
date_account_created            0
date_first_booking         186639
gender                          0
age                             0
signup_method                   0
signup_flow                     0
language                        0
affiliate_channel               0
affiliate_provider              0
first_affiliate_tracked         0
signup_app                      0
first_device_type               0
first_browser                   0
country_destination         62096
first_active_date               0
dlanguage_EN                    0
dlanguage_FR                    0
dlanguage_ES                    0
dlanguage_IT                    0
dlanguage_PT                    0
dlanguage_NL                    0
dlanguage_DE                    0
dlanguage_other                 0
create_month                    0
create_day                      0
create_dow                      0
first_month                     0
first_day                       0
first_dow     

In [49]:
# merge with session
merged_df = df.merge(session_df, left_on = 'id', right_index = True, how = 'left')
# fillna
fill_cols = session_df.columns.tolist()
merged_df[fill_cols] = merged_df[fill_cols].fillna(0)
merged_df.loc[merged_df['device_type'] == 0, 'device_type'] = np.nan

In [50]:
# merged with age and gender
# convert age to age_bucket
def age_bucket(x):
    if x>= 100:
        return '100+'
    else:
        if x < 10:
            a = ''
            b = x
        else:
            a = str(int(x//10))
            b = x%10
        if b <= 4:
            return a + '0-' + a + '4'
        else:
            return a + '5-' + a + '9'

merged_df['age_bucket'] = merged_df['age'].map(age_bucket)
merged_df = merged_df.merge(by_age_df, on = 'age_bucket', how = 'left')

In [70]:
# One-hot encoding for categorical variables
cate_feat_ls = ['gender', 'signup_method', 'signup_flow',
                'language', 'affiliate_channel', 'affiliate_provider',
                'first_affiliate_tracked', 'signup_app', 'first_device_type',
                'first_browser', 'device_type', 'age_bucket']
clean_df = pd.concat([pd.get_dummies(merged_df[cate_feat_ls]).copy(), merged_df[merged_df.columns.difference(cate_feat_ls)]], axis = 1)

# Model

In [85]:
# split train test
# use data after 2014-01-01
exclude_cols = ['id', 'date_account_created', 'first_active_date', 'date_first_booking', 'country_destination']

X_train = clean_df.loc[(clean_df['country_destination'].notna()) & (clean_df['date_account_created'] >= '2014-01-01'), 
                       clean_df.columns.difference(exclude_cols)]
y_train = clean_df.loc[(clean_df['country_destination'].notna()) & (clean_df['date_account_created'] >= '2014-01-01'), 
                       'country_destination']
X_test = clean_df.loc[(clean_df['country_destination'].isna()) & (clean_df['date_account_created'] >= '2014-01-01'), 
                       clean_df.columns.difference(exclude_cols)]

In [ ]:
# cross validation
# lgb_clf = lgb.LGBMClassifier()
# score = cross_val_score(lgb_clf, X_train, y_train, cv = 5, scoring = 'f1_weighted')
# print(score.mean())

In [96]:
lgb_clf = lgb.LGBMClassifier()
lgb_clf.fit(X_train, y_train)
# select features
model = SelectFromModel(lgb_clf, prefit = True)
X_train = model.transform(X_train)
X_test = model.transform(X_test)

feat_import_df = pd.DataFrame({'feature': X_train.columns, 'importance': lgb_clf.feature_importances_})
feat_import_df.sort_values(['importance'], ascending = False, inplace = True)
# Show top 20 features
feat_import_df.head(20)

In [ ]:
# # optuna for parameter tunning
# X_train = X_train[feat_import_df.loc[feat_import_df['importance'] > 10, 'feature'].tolist()]
# X_test = clean_df.loc[clean_df['country_destination'].isna(), X_train.columns]
# X_valid = X_train[60000:].copy()
# X_train = X_train[:60000]
# y_valid = y_train[60000:].copy()
# y_train = y_train[:60000]
# def objective(trial):
#     param = {
#         "objective": "multiclass",
#         "verbosity": -1,
#         "num_leaves": trial.suggest_int("num_leaves", 100, 300),
#         "feature_fraction": trial.suggest_float("feature_fraction", 0.4, 1.0),
#         "bagging_fraction": trial.suggest_float("bagging_fraction", 0.4, 1.0),
#         "bagging_freq": trial.suggest_int("bagging_freq", 1, 7),
#         "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 50, 100),
#         "max_depth": trial.suggest_int("max_depth", 20, 70),
#         "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
#         "n_estimators": trial.suggest_int("n_estimators", 100, 500),
#         "reg_alpha": trial.suggest_int("reg_alpha", 0, 1000),
#         "reg_lambda": trial.suggest_int("reg_lambda", 0, 1000)
#     }
    
#     lgb_reg = lgb.LGBMClassifier(**param)
#     lgb_reg.fit(X_train, y_train)
#     pred_df = pd.DataFrame(lgb_reg.predict(X_valid), columns = ['pred_country'])
#     pred_df['true_country'] = y_valid.values
#     error = sklearn.metrics.f1_score(pred_df['pred_country'], pred_df['true_country'], average = 'weighted')
#     return error

# study = optuna.create_study(direction="maximize")
# study.optimize(objective, n_trials=100)
# print(study.best_params)

In [91]:
param = {'num_leaves': 114,
                                'feature_fraction': 0.6032352513287674,
                                'bagging_fraction': 0.8799533044498802,
                                'bagging_freq': 1,
                                'min_data_in_leaf': 89,
                                'max_depth': 69,
                                'min_child_samples': 8,
                                'n_estimators': 210,
                                'reg_alpha': 37,
                                'reg_lambda': 709}

lgb_clf = lgb.LGBMClassifier(**{'num_leaves': 114,
                                'min_data_in_leaf': 89,
                                'n_estimators': 210,
                                'min_child_samples': 8,
                                'objective': 'multiclass',
                                'reg_alpha': 80})

xgb_clf = XGBClassifier(**{'objective': 'multi:softprob',
                           'n_estimators': 200,
                           'subsample': 0.8,
                           'learning_rate': 0.1,
                           'max_depth': None,
                           'reg_alpha': 100})

rf_clf = RandomForestClassifier(**{'n_estimators': 200})
# use voting classifier
voting_clf = VotingClassifier(estimators = [('lgb', lgb_clf), ('xgb', xgb_clf), ('rf', rf_clf)], voting = 'soft')
voting_clf.fit(X_train, y_train)

[LightGBM] [Warning] min_data_in_leaf is set=89, min_child_samples=8 will be ignored. Current value: min_data_in_leaf=89
[15:56:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


VotingClassifier(estimators=[('lgb',
                              LGBMClassifier(min_child_samples=8,
                                             min_data_in_leaf=89,
                                             n_estimators=210, num_leaves=114,
                                             objective='multiclass',
                                             reg_alpha=80)),
                             ('xgb',
                              XGBClassifier(base_score=None, booster=None,
                                            colsample_bylevel=None,
                                            colsample_bynode=None,
                                            colsample_bytree=None,
                                            enable_categorical=False,
                                            gamma=None, gpu_id=None,
                                            importance_type=None,
                                            int...
                                            min_chil

# Submit

In [102]:
# predict probability
pred_prob_df = pd.DataFrame(voting_clf.predict_proba(X_test_new), index = raw_test_df['id'].values, columns = np.sort(y_train.unique()))
# select 5 countries with the highest probabilities
pred_df = pred_prob_df.stack().reset_index().rename(columns = {'level_0': 'id', 'level_1': 'country', 0: 'prob'}).sort_values(['id', 'prob'], ascending = False).reset_index(drop = True)
use_index = []
for i in range(len(pred_df)):
    if i%12 < 5:
        use_index.append(i)

pred_df = pred_df.iloc[use_index][['id', 'country']]
submit_df = raw_test_df[['id']].merge(pred_df, on = 'id')
submit_df.to_csv('submission.csv', index = False)